In [14]:
import pandas as pd
import pickle
from PlotlyTools.Trace import TraceBuilder
import plotly.offline as pyo
from plotly.graph_objs import *
import plotly.plotly as py
from plotly import tools
import seaborn as sns
import matplotlib.pyplot as plt
import plotly.graph_objs as go
from plotly.tools import FigureFactory as FF
pyo.offline.init_notebook_mode()

In [277]:
def text_generator(data, columns=[], pattern=''):
    n_cols = len(columns)
    return data.loc[:, (columns)].apply(lambda x: pattern.format([x[columns[i]] for i in range(n_cols)]), axis=1)

def bar_trace_builder(x, y, color, color_line, width_line, text, legendgroup):#, name, legendgroup, symbol, size):
    trace = {
            "type": "bar",
            "x": x,
            "y": y,
            "text": text,
            'hoverinfo': "x+y+text",
            "showlegend": False,
            "legendgroup":legendgroup,
            "orientation": 'h',
            "marker": {
                "color": color,
                "line": {
                    "color": color_line,
                    "width": width_line,
                }
            }
    }
    return trace

def line_trace_evictions_builder(x, y, color, name, legendgroup):#, text):#, legendgroup, showlegend):#, symbol, size):
    trace = {
            "type": "scatter",
            "mode": "lines",
            "x": x,
            "y": y,
            "name": name,
            #"text": text,
            "legendgroup": legendgroup,
            #"showlegend": showlegend,
            'hoverinfo': "text+y",
            "marker": {
                "color": color,
                "line": {"width": 4}
            }
    }
    return trace

def line_trace_rent_builder(x, y, color, name, legendgroup):#, text):#, legendgroup, showlegend):#, symbol, size):
    trace = {
            "type": "scatter",
            "mode": "lines",
            "x": x,
            "y": y,
            "name": name,
            #"text": text,
            "legendgroup": legendgroup,
            #"showlegend": showlegend,
            'hoverinfo': "text+y",
            "yaxis": 'y6',
            "marker": {
                "color": color,
                "line": {"width": 4}
            }
    }
    return trace

def line_trace_listings_builder(x, y, color, name, legendgroup):#, text):#, legendgroup, showlegend):#, symbol, size):
    trace = {
            "type": "scatter",
            "mode": "lines",
            "x": x,
            "y": y,
            "name": name,
            #"text": text,
            "legendgroup": legendgroup,
            #"showlegend": showlegend,
            "yaxis": 'y7',
            'hoverinfo': "text+y",
            "marker": {
                "color": color,
                "line": {"width": 4}
            }
    }
    return trace

def line_trace_area_host(x, y, color, name, legendgroup):#, text):#, legendgroup, showlegend):#, symbol, size):
    trace = {
            "mode": "lines",
            "x": x,
            "y": y,
            "name": name,
            #"text": text,
            "legendgroup": legendgroup,
            #"showlegend": showlegend,
            'hoverinfo': "text+y",
            "fill":'tonexty',
            "line": {"color": color}
    }
    return trace

def choropleth_trace_builder():
    trace = {"type": 'choropleth',
             "colorscale": scl,
             "autocolorscale": False,
             "locations": df['code'],
             "z": df['total exports'].astype(float),
             "locationmode": 'USA-states',
             "text": df['text'],
             "marker": {
                    "line": {
                        "color": 'rgb(255,255,255)',
                        "width": 2}
             },
             "colorbar": {"title": "Millions USD"}
            }
    return trace

### Load data airbnb and rent prices

In [278]:
# Load airbnb data
n_revs_type_evol_ = pd.read_csv('../price_m2_madrid_districts_per_year/data/n_reviews_year_host_type.csv')
n_list_type_evol = pd.read_csv('../price_m2_madrid_districts_per_year/data/n_listings_year_host_type_room_type.csv')
n_list_inhab = pd.read_csv('../price_m2_madrid_districts_per_year/data/n_airbnb_listings_1000_inhab_district.csv')
n_list_year = n_list_type_evol.loc[:,('first_review_year',
                                      'host_total_listings_count')].groupby(['first_review_year'], 
                                                                            as_index=False).sum()

# Load rent prices
rent_prices = pd.read_csv("../price_m2_madrid_districts_per_year/data/rent_price_m2_districts_ratio.csv")

# Load number of mortage executions
mort_executions = pd.read_csv("../price_m2_madrid_districts_per_year/data/c_madrid_ejec_hipotec_cgpj.csv")
mort_executions['mortage_executions'] = mort_executions['mortage_executions'].astype(int)

In [279]:
# Assign a label to districts depending on the level of impact that airbnb is having
n_list_inhab = n_list_inhab.sort_values(by='n_list_inh_1000').reset_index(drop=True)
q_1_2_3 = n_list_inhab['n_list_inh_1000'].quantile([.25, .5, .75]).get_values()
n_list_inhab['airbnb_level'] = 'low'
n_list_inhab.loc[n_list_inhab['n_list_inh_1000'] >= q_1_2_3[2], ('airbnb_level')] = 'high'
n_list_inhab.loc[(n_list_inhab['n_list_inh_1000'] < q_1_2_3[2]) & \
                 (n_list_inhab['n_list_inh_1000'] > q_1_2_3[1]), ('airbnb_level')] = 'medium'
n_list_inhab.loc[n_list_inhab['n_list_inh_1000'] > 8, ('airbnb_level')] = 'extreme'

In [280]:
# Plot design parameters
colors_airbnb_level = {
    "extreme": "rgb(7,77,101)",
    "high": "rgb(65,187,197)",
    "medium": "rgb(114,229,239)",
    "low": "rgb(203,213,231)"
}
color_line = "rgba(0,0,0,0)"
width_line = 4
legendgroup = "listingsinhabitants"

In [281]:
# Build barplot of number of listings per 1000 inhabitants
trace_airbnb_level = bar_trace_builder(y=n_list_inhab['district'], x=n_list_inhab['n_list_inh_1000'], 
                                color=[colors_airbnb_level[label] for label in n_list_inhab['airbnb_level']],
                                color_line=color_line, width_line=width_line, 
                                text=["<b>"+i+"</b>" for i in n_list_inhab['airbnb_level']], legendgroup=legendgroup)
layout_airbnb_level = {
    "xaxis": {
        "title": "Number of Airbnb listings per 1000 Inhabitatns",
        'showgrid': False
    },
    "yaxis": {
        'showgrid': False
    },
    "showlegend": False,
    "orientation": 'h',
    "margin": {'l': 140}
}
figure_airbnb_level = dict(data = [trace_airbnb_level], layout = layout_airbnb_level)

In [282]:
# Build lineplot comparing number of evictions with number of listings in airbnb
legendgroup = "evictions"
mort_executions_ = mort_executions.copy()
evictions = line_trace_evictions_builder(x=mort_executions_['year'], 
                                         y=mort_executions_['mortage_executions'], color="rgb(183,64,92)",
                                         name="evictions", legendgroup=legendgroup)

n_list_year_ = n_list_year[n_list_year['first_review_year'] != 2018]
listings = line_trace_listings_builder(x=n_list_year_['first_review_year'], 
                                       y=n_list_year_['host_total_listings_count'], color="rgb(7,77,101)",
                                      name="Airbnb listings", legendgroup=legendgroup)
mortab_n_listings = {
    "title": 'Evolution of number of evictions and number of Airbnb listings [2010-2017]',
        "yaxis": {
            "title": "Number of Mortage Executions",
            "titlefont": {
                "color": 'rgb(183,64,92)'
            },
            "tickfont": {
                "color": 'rgb(183,64,92)'
            },
            'showgrid': False
        },
        "yaxis2": {
            "title": "Number of Airbnb listings",
            "titlefont": {
                "color": 'rgb(7,77,101)'
            },
            "tickfont": {
                "color": 'rgb(7,77,101)'
            },
            "overlaying": 'y',
            "side": 'right',
            'showgrid': False
        },
    "xaxis": {'showgrid': False},
    "xaxis2": {'showgrid': False},
    "hovermode": "closest"
}
fig_mortab_n_listings = dict(data=[evictions,listings], layout=mortab_n_listings)

In [283]:
# Build areaplot comparing listings evolution per host type
legendgroup = "hostype"
n_share = n_list_type_evol.loc[n_list_type_evol['host_type']=='share_airbnb', 
                     ("host_total_listings_count","first_review_year")].rename(columns=\
                                                                {'host_total_listings_count':'n_list_share'})
n_flat = n_list_type_evol.loc[n_list_type_evol['host_type']=='flat_airbnb', 
                     ("host_total_listings_count","first_review_year")].rename(columns=\
                                                                {'host_total_listings_count':'n_list_flat'})
n_business = n_list_type_evol.loc[n_list_type_evol['host_type']=='business_airbnb', 
                     ("host_total_listings_count","first_review_year")].rename(columns=\
                                                                {'host_total_listings_count':'n_list_business'})

n_list_host = n_share.merge(n_flat, left_on='first_review_year', right_on="first_review_year")
n_list_host = n_list_host.merge(n_business, left_on='first_review_year', right_on="first_review_year")
n_list_host.loc[:,("n_list_share","n_list_flat","n_list_business")] = n_list_host.loc[:,
                                        ("n_list_share","n_list_flat","n_list_business")].cumsum(axis=1)
n_list_host = n_list_host[n_list_host["first_review_year"]!=2018]

colors_area = ["rgb(17,204,220)", "rgb(192,216,231)", "rgb(37,102,118)"]
columns = ['n_list_share','n_list_flat','n_list_business']
names = ['host only sharing','host renting one entire flat','host renting > 1 flat']
traces_host_type = []
for i, host in enumerate(columns):
    traces_host_type.append(line_trace_area_host(x=n_list_host['first_review_year'], y=n_list_host[host], 
                                                 color=colors_area[i], name=names[i], legendgroup=legendgroup))
layout_airbnb_host = {
    "title": "Number of listings per type of host [2011-2017]",
    "xaxis": {
        'showgrid': False
    },
    "yaxis": {
        "title": "Number of listings",
        'showgrid': False
    }
}
fig_listing_host = dict(data=traces_host_type, layout=layout_airbnb_host)

In [284]:
# Build lineplots comparing listings evolution with rent prices
legendgroup = "rentprices"
n_business_ = n_business[n_business['first_review_year']<2018]
trace_n_business = line_trace_evictions_builder(x=n_business_['first_review_year'], 
                                         y=n_business_['n_list_business'], color="rgb(7,77,101)",
                                         name="Listings hosts renting > 1 flat",legendgroup=legendgroup)
rent_prices_ = rent_prices.loc[:,("price_m2","year")].groupby(['year'], as_index=False).mean()
trace_rent = line_trace_rent_builder(x=rent_prices_['year'], 
                                         y=rent_prices_['price_m2'], color="rgb(183,64,92)",
                                         name="Mean rental price per m2",legendgroup=legendgroup)
layout_listing_rent = {
    "title": 'Evolution of listings for Airbnb hosts with > 1 flat and rental prices [2010-2017]',
        "yaxis": {
            "title": "Number of Airbnb listings",
            "titlefont": {
                "color": 'rgb(7,77,101)'
            },
            "tickfont": {
                "color": 'rgb(7,77,101)'
            },
            'showgrid': False
        },
        "yaxis2": {
            "title": "Price of rent per m2 (Euros)",
            "titlefont": {
                "color": 'rgb(183,64,92)'
            },
            "tickfont": {
                "color": 'rgb(183,64,92)'
            },
            "overlaying": 'y',
            "side": 'right',
            'showgrid': False
        },
    "xaxis": {'showgrid': False},
    "xaxis2": {'showgrid': False},
    "hovermode": "closest"
}
fig_listings_rent = dict(data=[trace_n_business,trace_rent], layout=layout_listing_rent)

In [220]:
#py.iplot(fig_listings_rent, filename="Trend on rental prices and Airbng business hosts", fileopt="overwrite")

### Build individual plots

In [85]:
pyo.iplot(figure_airbnb_level)

In [109]:
pyo.iplot(fig_mortab_n_listings)

In [181]:
#py.iplot(fig_listing_host, filename="Trend on rental prices ", fileopt="overwrite")pyo.iplot(fig_listing_host)

In [222]:
pyo.iplot(fig_listings_rent)

In [183]:
#py.iplot(fig_listing_host, filename="Number of Airbnb listings per host type", fileopt="overwrite")

### Build plots for dashboard

In [218]:
pyo.iplot(figure_income)

In [219]:
pyo.iplot(figures_inhabitants[1])

In [241]:
#py.iplot(figure_income, filename="net_income_madrid_districts")

In [242]:
#for i in range(0,5):
#    py.iplot(figures_inhabitants[i], filename="evolution_madrid_population_" + age_ranges[i], fileopt="overwrite")

### Build dashboard

In [380]:
fig = tools.make_subplots(cols=1, rows=4, vertical_spacing = 0.08,
                         subplot_titles = ["Number of Airbnb listings per 1000 Inhabitatns",
                                          "Number of listings per type of host [2011-2017]",
                                          'Evolution of number of evictions and number of Airbnb listings [2010-2017]',
                                          'Evolution of listings for Airbnb hosts with > 1 flat and rental prices [2010-2017]'])
fig.append_trace(trace_airbnb_level, row=1, col=1)
fig.append_trace(traces_host_type[0], row=2, col=1)
fig.append_trace(traces_host_type[1], row=2, col=1)
fig.append_trace(traces_host_type[2], row=2, col=1)
fig.append_trace(evictions, row=3, col=1)
fig.append_trace(listings, row=3, col=1)
fig.append_trace(trace_n_business, row=4, col=1)
fig.append_trace(trace_rent, row=4, col=1)

# correct layout
fig['layout'].update(height=1500, width=1000, title='Impact of Airbnb on rental prices and evictions')
y_axis = ['yaxis1', 'yaxis2', 'yaxis3', 'yaxis4','yaxis7','yaxis8']
x_axis = ['xaxis1', 'xaxis2', 'xaxis3', 'xaxis4']
fig['data'][5].update(yaxis='y7')
fig['data'][7].update(yaxis='y8')

fig['layout']['yaxis7'].update(**fig['layout']['yaxis3'], side = "right", overlaying='y3')
fig['layout']['yaxis8'].update(**fig['layout']['yaxis4'], side = "right", overlaying='y4')

y_axis_titles = ["Number of Airbnb listings","Number of Mortage Executions","Number of Airbnb listings",
                "Number of Airbnb listings","Price of rent per m2 (Euros)"]
for i, axis in enumerate(y_axis[1:]):
    fig['layout'][axis].update(title = y_axis_titles[i], showgrid = False)
fig['layout']['xaxis1'].update(title="Number of Airbnb listings per 1000 Inhabitatns")
    
fig['layout']['yaxis3']["tickfont"].update(color="rgb(183,64,92)")
fig['layout']['yaxis4']["tickfont"].update(color="rgb(7,77,101)")
fig['layout']['yaxis7']["tickfont"].update(color="rgb(7,77,101)")
fig['layout']['yaxis8']["tickfont"].update(color="rgb(183,64,92)")
fig['layout']['yaxis3']["titlefont"].update(color="rgb(183,64,92)")
fig['layout']['yaxis4']["titlefont"].update(color="rgb(7,77,101)")
fig['layout']['yaxis7']["titlefont"].update(color="rgb(7,77,101)")
fig['layout']['yaxis8']["titlefont"].update(color="rgb(183,64,92)")

fig['layout']['margin'].update(l=150)
fig['layout']['yaxis1'].update(dtick= 1)
#y_labels = ["Net income (euros)", "Number of Inhabitants", "Number of Inhabitants",
#           "Number of Inhabitants", "Number of Inhabitants", "Number of Inhabitants"]
#for i in range(0,6):
#    fig['layout'][y_axis[i]].update(title = y_labels[i], showgrid = False)

This is the format of your plot grid:
[ (1,1) x1,y1 ]
[ (2,1) x2,y2 ]
[ (3,1) x3,y3 ]
[ (4,1) x4,y4 ]



In [382]:
pyo.iplot(fig)

In [384]:
#py.iplot(fig, filename="Impact of Airbnb on rental prices and evictions", fileopt="overwrite")